# Scraping reviews from Reclame Aqui website

## Imports

In [74]:
import requests
from bs4 import BeautifulSoup
import numpy as np
import pandas as pd
from selenium import webdriver
from selenium.webdriver.chrome.options import Options
import time
import math
#import matplotlib.pyplot as plt
#%matplotlib inline

## Create driver

In [2]:
options = Options()
options.add_argument('--headless')
options.add_argument('--disable-gpu')
driver = webdriver.Chrome(options=options)

## Define Functions

In [3]:
def create_url(company, page):
    return f'https://www.reclameaqui.com.br/empresa/{company}/lista-reclamacoes/?pagina={page}'

In [32]:
def get_soup(driver,url):
    driver.get(url)
    driver.execute_script("window.scrollTo(0, document.body.scrollHeight);var lenOfPage=document.body.scrollHeight;return lenOfPage;")
    time.sleep(1)
    soup = BeautifulSoup(driver.page_source, "html.parser")
    return soup

In [5]:
def get_complaints(soup):
    complaints = soup.find_all(class_="link-complain-id-complains")
    return complaints

In [6]:
def get_titles(complaints):
    title_list = []
    for i in range(len(complaints)):
        title_list.append(complaints[i].text.strip())
    return title_list

In [7]:
def get_links(complaints):
    link_list = []
    start_url = 'https://www.reclameaqui.com.br'
    for i in range(len(complaints)):
        link = (start_url + complaints[i].get('href'))
        link_list.append(link)
    return link_list

In [8]:
def get_content(soup):
    try:
        content = soup.find_all('p', class_="ng-binding")[9].text.strip()
        return content
    except:
        return 'NA'

In [9]:
def get_titles_and_links(company, num_pages, driver):
    titles = []
    links = []
    for i in range(1, num_pages+1):
        page_url = create_url(company, i)
        page_soup = get_soup(driver, page_url)
        page_complaints = get_complaints(page_soup)
        page_titles = get_titles(page_complaints)
        page_links = get_links(page_complaints)
        
        titles += page_titles
        links += page_links
        
    return titles, links

In [10]:
def get_content_list(driver, links):
    content_list = []
    for i in range(len(links)):
        url = links[i]
        soup = get_soup(driver,url)
        print(f'Retrieved {i+1} of {len(links)}')
        content = get_content(soup)
        content_list.append(content)
    return content_list

## Test Functions

In [29]:
titles, links = get_titles_and_links('upnid',2,driver)

<html class="ng-scope" lang="pt-BR" ng-app="rawebApp"><head><style type="text/css">[uib-typeahead-popup].dropdown-menu{display:block;}</style><style type="text/css">.uib-time input{width:50px;}</style><style type="text/css">[uib-tooltip-popup].tooltip.top-left > .tooltip-arrow,[uib-tooltip-popup].tooltip.top-right > .tooltip-arrow,[uib-tooltip-popup].tooltip.bottom-left > .tooltip-arrow,[uib-tooltip-popup].tooltip.bottom-right > .tooltip-arrow,[uib-tooltip-popup].tooltip.left-top > .tooltip-arrow,[uib-tooltip-popup].tooltip.left-bottom > .tooltip-arrow,[uib-tooltip-popup].tooltip.right-top > .tooltip-arrow,[uib-tooltip-popup].tooltip.right-bottom > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.top-left > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.top-right > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.bottom-left > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.bottom-right > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.left-top > .tooltip-arrow,[uib-tooltip-html-popup].

<html class="ng-scope" lang="pt-BR" ng-app="rawebApp"><head><style type="text/css">[uib-typeahead-popup].dropdown-menu{display:block;}</style><style type="text/css">.uib-time input{width:50px;}</style><style type="text/css">[uib-tooltip-popup].tooltip.top-left > .tooltip-arrow,[uib-tooltip-popup].tooltip.top-right > .tooltip-arrow,[uib-tooltip-popup].tooltip.bottom-left > .tooltip-arrow,[uib-tooltip-popup].tooltip.bottom-right > .tooltip-arrow,[uib-tooltip-popup].tooltip.left-top > .tooltip-arrow,[uib-tooltip-popup].tooltip.left-bottom > .tooltip-arrow,[uib-tooltip-popup].tooltip.right-top > .tooltip-arrow,[uib-tooltip-popup].tooltip.right-bottom > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.top-left > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.top-right > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.bottom-left > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.bottom-right > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.left-top > .tooltip-arrow,[uib-tooltip-html-popup].

In [30]:
titles

['comprei e não recebi',
 'Não compre na FLIPCART',
 'Comprei nao recebi',
 'Cobrança  indevida.',
 'Produto não entregue',
 'Fiz uma compra na Upnid em 26.01.2021 e até o  momento não recebi o produto',
 'Empresa não idônea.',
 'Upnid - tv-global',
 'Produto não recebido',
 '[Editado pelo Reclame Aqui]',
 'Site Shopmakee não aparece mais',
 'Comprei um kit de alongamento e ainda não enviaram',
 'Compra sem confirmação por e-mail',
 'Compra sem retorno',
 'MODELADOR ALUVI AIRWRAP 5 EM 1 × 1',
 'Produto não entregue',
 'Comprei e não recebi',
 'Não  recebi o produto',
 'compra TV global',
 'faggio store']

In [13]:
links

['https://www.reclameaqui.com.br/upnid/comprei-e-nao-recebi_DLMdwWwuv0C85DcZ/',
 'https://www.reclameaqui.com.br/upnid/nao-compre-na-flipcart_M6c3cnBwGvE8RNmP/',
 'https://www.reclameaqui.com.br/upnid/comprei-nao-recebi_wn7QFAzRBJO2pwup/',
 'https://www.reclameaqui.com.br/upnid/cobranca-indevida_lqWsHt97_dkZeBNF/',
 'https://www.reclameaqui.com.br/upnid/produto-nao-entregue_PJfWvuC7cvdc4LuM/',
 'https://www.reclameaqui.com.br/upnid/fiz-uma-compra-na-upnid-em-26-01-2021-e-ate-o-momento-nao-recebi-o-produto_DHLCzGSQ4hRdC2po/',
 'https://www.reclameaqui.com.br/upnid/empresa-nao-idonea_G2ZA0-zJIJgCRli7/',
 'https://www.reclameaqui.com.br/upnid/upnid-tv-global_7YmhsMES98qHeKfa/',
 'https://www.reclameaqui.com.br/upnid/produto-nao-recebido_IVUyV4L-uOJlnDim/',
 'https://www.reclameaqui.com.br/upnid/titulo_PelzEXcDwMywOdRF/',
 'https://www.reclameaqui.com.br/upnid/site-shopmakee-nao-aparece-mais_ZCQCbWAfaWGCRHEI/',
 'https://www.reclameaqui.com.br/upnid/comprei-um-kit-de-alongamento-e-ainda-na

In [14]:
contents = get_content_list(driver,links)

<html class="ng-scope" lang="pt-BR" ng-app="rawebApp"><head><style type="text/css">[uib-typeahead-popup].dropdown-menu{display:block;}</style><style type="text/css">.uib-time input{width:50px;}</style><style type="text/css">[uib-tooltip-popup].tooltip.top-left > .tooltip-arrow,[uib-tooltip-popup].tooltip.top-right > .tooltip-arrow,[uib-tooltip-popup].tooltip.bottom-left > .tooltip-arrow,[uib-tooltip-popup].tooltip.bottom-right > .tooltip-arrow,[uib-tooltip-popup].tooltip.left-top > .tooltip-arrow,[uib-tooltip-popup].tooltip.left-bottom > .tooltip-arrow,[uib-tooltip-popup].tooltip.right-top > .tooltip-arrow,[uib-tooltip-popup].tooltip.right-bottom > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.top-left > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.top-right > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.bottom-left > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.bottom-right > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.left-top > .tooltip-arrow,[uib-tooltip-html-popup].

<html class="ng-scope" lang="pt-BR" ng-app="rawebApp"><head><style type="text/css">[uib-typeahead-popup].dropdown-menu{display:block;}</style><style type="text/css">.uib-time input{width:50px;}</style><style type="text/css">[uib-tooltip-popup].tooltip.top-left > .tooltip-arrow,[uib-tooltip-popup].tooltip.top-right > .tooltip-arrow,[uib-tooltip-popup].tooltip.bottom-left > .tooltip-arrow,[uib-tooltip-popup].tooltip.bottom-right > .tooltip-arrow,[uib-tooltip-popup].tooltip.left-top > .tooltip-arrow,[uib-tooltip-popup].tooltip.left-bottom > .tooltip-arrow,[uib-tooltip-popup].tooltip.right-top > .tooltip-arrow,[uib-tooltip-popup].tooltip.right-bottom > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.top-left > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.top-right > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.bottom-left > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.bottom-right > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.left-top > .tooltip-arrow,[uib-tooltip-html-popup].

<html class="ng-scope" lang="pt-BR" ng-app="rawebApp"><head><style type="text/css">[uib-typeahead-popup].dropdown-menu{display:block;}</style><style type="text/css">.uib-time input{width:50px;}</style><style type="text/css">[uib-tooltip-popup].tooltip.top-left > .tooltip-arrow,[uib-tooltip-popup].tooltip.top-right > .tooltip-arrow,[uib-tooltip-popup].tooltip.bottom-left > .tooltip-arrow,[uib-tooltip-popup].tooltip.bottom-right > .tooltip-arrow,[uib-tooltip-popup].tooltip.left-top > .tooltip-arrow,[uib-tooltip-popup].tooltip.left-bottom > .tooltip-arrow,[uib-tooltip-popup].tooltip.right-top > .tooltip-arrow,[uib-tooltip-popup].tooltip.right-bottom > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.top-left > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.top-right > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.bottom-left > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.bottom-right > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.left-top > .tooltip-arrow,[uib-tooltip-html-popup].

<html class="ng-scope" lang="pt-BR" ng-app="rawebApp"><head><style type="text/css">[uib-typeahead-popup].dropdown-menu{display:block;}</style><style type="text/css">.uib-time input{width:50px;}</style><style type="text/css">[uib-tooltip-popup].tooltip.top-left > .tooltip-arrow,[uib-tooltip-popup].tooltip.top-right > .tooltip-arrow,[uib-tooltip-popup].tooltip.bottom-left > .tooltip-arrow,[uib-tooltip-popup].tooltip.bottom-right > .tooltip-arrow,[uib-tooltip-popup].tooltip.left-top > .tooltip-arrow,[uib-tooltip-popup].tooltip.left-bottom > .tooltip-arrow,[uib-tooltip-popup].tooltip.right-top > .tooltip-arrow,[uib-tooltip-popup].tooltip.right-bottom > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.top-left > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.top-right > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.bottom-left > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.bottom-right > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.left-top > .tooltip-arrow,[uib-tooltip-html-popup].

<html class="ng-scope" lang="pt-BR" ng-app="rawebApp"><head><style type="text/css">[uib-typeahead-popup].dropdown-menu{display:block;}</style><style type="text/css">.uib-time input{width:50px;}</style><style type="text/css">[uib-tooltip-popup].tooltip.top-left > .tooltip-arrow,[uib-tooltip-popup].tooltip.top-right > .tooltip-arrow,[uib-tooltip-popup].tooltip.bottom-left > .tooltip-arrow,[uib-tooltip-popup].tooltip.bottom-right > .tooltip-arrow,[uib-tooltip-popup].tooltip.left-top > .tooltip-arrow,[uib-tooltip-popup].tooltip.left-bottom > .tooltip-arrow,[uib-tooltip-popup].tooltip.right-top > .tooltip-arrow,[uib-tooltip-popup].tooltip.right-bottom > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.top-left > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.top-right > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.bottom-left > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.bottom-right > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.left-top > .tooltip-arrow,[uib-tooltip-html-popup].

...

<html class="ng-scope" lang="pt-BR" ng-app="rawebApp"><head><style type="text/css">[uib-typeahead-popup].dropdown-menu{display:block;}</style><style type="text/css">.uib-time input{width:50px;}</style><style type="text/css">[uib-tooltip-popup].tooltip.top-left > .tooltip-arrow,[uib-tooltip-popup].tooltip.top-right > .tooltip-arrow,[uib-tooltip-popup].tooltip.bottom-left > .tooltip-arrow,[uib-tooltip-popup].tooltip.bottom-right > .tooltip-arrow,[uib-tooltip-popup].tooltip.left-top > .tooltip-arrow,[uib-tooltip-popup].tooltip.left-bottom > .tooltip-arrow,[uib-tooltip-popup].tooltip.right-top > .tooltip-arrow,[uib-tooltip-popup].tooltip.right-bottom > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.top-left > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.top-right > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.bottom-left > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.bottom-right > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.left-top > .tooltip-arrow,[uib-tooltip-html-popup].

<html class="ng-scope" lang="pt-BR" ng-app="rawebApp"><head><style type="text/css">[uib-typeahead-popup].dropdown-menu{display:block;}</style><style type="text/css">.uib-time input{width:50px;}</style><style type="text/css">[uib-tooltip-popup].tooltip.top-left > .tooltip-arrow,[uib-tooltip-popup].tooltip.top-right > .tooltip-arrow,[uib-tooltip-popup].tooltip.bottom-left > .tooltip-arrow,[uib-tooltip-popup].tooltip.bottom-right > .tooltip-arrow,[uib-tooltip-popup].tooltip.left-top > .tooltip-arrow,[uib-tooltip-popup].tooltip.left-bottom > .tooltip-arrow,[uib-tooltip-popup].tooltip.right-top > .tooltip-arrow,[uib-tooltip-popup].tooltip.right-bottom > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.top-left > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.top-right > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.bottom-left > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.bottom-right > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.left-top > .tooltip-arrow,[uib-tooltip-html-popup].

<html class="ng-scope" lang="pt-BR" ng-app="rawebApp"><head><style type="text/css">[uib-typeahead-popup].dropdown-menu{display:block;}</style><style type="text/css">.uib-time input{width:50px;}</style><style type="text/css">[uib-tooltip-popup].tooltip.top-left > .tooltip-arrow,[uib-tooltip-popup].tooltip.top-right > .tooltip-arrow,[uib-tooltip-popup].tooltip.bottom-left > .tooltip-arrow,[uib-tooltip-popup].tooltip.bottom-right > .tooltip-arrow,[uib-tooltip-popup].tooltip.left-top > .tooltip-arrow,[uib-tooltip-popup].tooltip.left-bottom > .tooltip-arrow,[uib-tooltip-popup].tooltip.right-top > .tooltip-arrow,[uib-tooltip-popup].tooltip.right-bottom > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.top-left > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.top-right > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.bottom-left > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.bottom-right > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.left-top > .tooltip-arrow,[uib-tooltip-html-popup].

<html class="ng-scope" lang="pt-BR" ng-app="rawebApp"><head><style type="text/css">[uib-typeahead-popup].dropdown-menu{display:block;}</style><style type="text/css">.uib-time input{width:50px;}</style><style type="text/css">[uib-tooltip-popup].tooltip.top-left > .tooltip-arrow,[uib-tooltip-popup].tooltip.top-right > .tooltip-arrow,[uib-tooltip-popup].tooltip.bottom-left > .tooltip-arrow,[uib-tooltip-popup].tooltip.bottom-right > .tooltip-arrow,[uib-tooltip-popup].tooltip.left-top > .tooltip-arrow,[uib-tooltip-popup].tooltip.left-bottom > .tooltip-arrow,[uib-tooltip-popup].tooltip.right-top > .tooltip-arrow,[uib-tooltip-popup].tooltip.right-bottom > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.top-left > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.top-right > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.bottom-left > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.bottom-right > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.left-top > .tooltip-arrow,[uib-tooltip-html-popup].

<html class="ng-scope" lang="pt-BR" ng-app="rawebApp"><head><style type="text/css">[uib-typeahead-popup].dropdown-menu{display:block;}</style><style type="text/css">.uib-time input{width:50px;}</style><style type="text/css">[uib-tooltip-popup].tooltip.top-left > .tooltip-arrow,[uib-tooltip-popup].tooltip.top-right > .tooltip-arrow,[uib-tooltip-popup].tooltip.bottom-left > .tooltip-arrow,[uib-tooltip-popup].tooltip.bottom-right > .tooltip-arrow,[uib-tooltip-popup].tooltip.left-top > .tooltip-arrow,[uib-tooltip-popup].tooltip.left-bottom > .tooltip-arrow,[uib-tooltip-popup].tooltip.right-top > .tooltip-arrow,[uib-tooltip-popup].tooltip.right-bottom > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.top-left > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.top-right > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.bottom-left > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.bottom-right > .tooltip-arrow,[uib-tooltip-html-popup].tooltip.left-top > .tooltip-arrow,[uib-tooltip-html-popup].

In [15]:
contents

['comprei um relogio na empresa escandalo store pelo instagram e não recebi, ate o watszap não atendem mais',
 'Dia 15.03.21 comprei no site flipcart um esfolicare no valor de R$ 48,99 fiz o pagamento parcelado no meu cartão de crédito, recebi a confirmação do pagamento e me informaram o número do pedido 9256, como não recebi o código do rastreio, mandei um email para contatoflipcart@gmail.com e nunca me responderam .',
 'Boa tarde Fiz pagamento de um produto que comprei com voces dia 01/12/2020. Uma escova. Mas ate o momento nao recebi nada. Sao praticamente 4 meses acho uma falta de consideraçao. Gostaria de ter uma posiçao de voces. Pois com certeza o dinheiro chegou pois paguei. Estou entrando em contato e espero resposta para que nao precisar procurar direito de consumidor. Grata, vanessa',
 'Verifiquei que foi debitado no meu cartão de crédito 3 parcelas de $655,80.Acontece que não efetuei compra alguma nesse valor. Gostaria que vcs esclarecessem o porque desse débito.',
 'Fiz um

## Create class

In [102]:
class ReclameAqui:
    
    def __init__(self, company, num_pages):
        self.company = company
        self.num_pages = num_pages
        self.max_pages = None
        self.driver = None
        self.titles = []
        self.links = []
        
    def build_driver(self):
        options = Options()
        options.add_argument('--headless')
        options.add_argument('--disable-gpu')
        self.driver = webdriver.Chrome(options=options)
        
    def get_max_pages(self):
        if not self.driver:
            print('You need to initialize a driver. Call method ".initialize()" first.')
            return
        results_per_page = 10
        page_url = create_url(self.company, 1)
        soup = get_soup(self.driver, page_url)
        complaints = int(soup.find_all('span', class_="company-index-label-value")[0].text.strip())
        self.max_pages = math.ceil(complaints / results_per_page)
        
    def initialize(self):
        self.build_driver()
        self.get_max_pages()
        
    def get_titles_and_links(self):
        if not self.driver:
            print('You need to initialize a driver. Call method ".initialize()" first.')
            return
        for i in range(1, self.num_pages+1):
            page_url = create_url(self.company, i)
            page_soup = get_soup(self.driver, page_url)
            page_complaints = get_complaints(page_soup)
            page_titles = get_titles(page_complaints)
            page_links = get_links(page_complaints)
            self.titles += page_titles
            self.links += page_links
        return self.titles, self.links

In [96]:
ra = ReclameAqui('upnid',2)

In [97]:
ra.driver

In [98]:
ra.get_titles_and_links()

You need to initialize a driver. Call method ".initialize()" first.


In [99]:
ra.initialize()

In [100]:
ra.driver

<selenium.webdriver.chrome.webdriver.WebDriver (session="445a18f01157d070f90e30376c6591da")>

In [101]:
ra.get_titles_and_links()

(['comprei e não recebi',
  'Não compre na FLIPCART',
  'Comprei nao recebi',
  'Cobrança  indevida.',
  'Produto não entregue',
  'Fiz uma compra na Upnid em 26.01.2021 e até o  momento não recebi o produto',
  'Empresa não idônea.',
  'Upnid - tv-global',
  'Produto não recebido',
  '[Editado pelo Reclame Aqui]',
  'Site Shopmakee não aparece mais',
  'Comprei um kit de alongamento e ainda não enviaram',
  'Compra sem confirmação por e-mail',
  'Compra sem retorno',
  'MODELADOR ALUVI AIRWRAP 5 EM 1 × 1',
  'Produto não entregue',
  'Comprei e não recebi',
  'Não  recebi o produto',
  'compra TV global',
  'faggio store'],
 ['https://www.reclameaqui.com.br/upnid/comprei-e-nao-recebi_DLMdwWwuv0C85DcZ/',
  'https://www.reclameaqui.com.br/upnid/nao-compre-na-flipcart_M6c3cnBwGvE8RNmP/',
  'https://www.reclameaqui.com.br/upnid/comprei-nao-recebi_wn7QFAzRBJO2pwup/',
  'https://www.reclameaqui.com.br/upnid/cobranca-indevida_lqWsHt97_dkZeBNF/',
  'https://www.reclameaqui.com.br/upnid/produt